# Q&A 모듈 테스트
전체 모듈에 대한 성능을 테스트 합니다.

In [1]:
import sys
## Root 파일(.py)을 Import 하기
sys.path.append("../")

In [2]:
from qna_adaptor import QuestionAnswerResponsor
from scrap import get_wiki_data, get_blog_data
from wiki_convert import Korquad2_Converter
from blog_convert import Blog_Converter
import pandas as pd

In [4]:
#한글 폰트 사용
from matplotlib import font_manager,rc
import matplotlib
import matplotlib.pyplot as plt
#폰트 경로
#font_path = "C:/Windows/Fonts/H2GTRM.TTF"
#폰트 이름 얻어오기
#font_name = font_manager.FontProperties(fname=font_path).get_name()
#font 설정
#matplotlib.rc('font',family=font_name)

## 모듈 테스트 QA 데이터
QA_testset은 8가지 카테고리를 갖고 있는 총 100개 데이터셋입니다. 질문과 짧은 답변으로만 이루어져 있으므로 Q&A 시스템을 통해 나온 문장에 답변이 있는지에 대한 간단한 모듈테스트에 적합합니다.

In [5]:
data_path = 'QA_testset.csv'
test_df = pd.read_csv(data_path)

In [6]:
test_df['카테고리'].unique()

array(['역사', '경제경영', '사회', '정치', '과학', '문화스포츠', '인문학', '기타'], dtype=object)

In [7]:
test_df.head()

카테고리                  question answer
0   역사              고구려를 건국한 왕은?     주몽
1   역사          과거제를 처음 도입한 시대는?   고려시대
2   역사             훈민정음을 창제한 왕은?  세종대왕 
3   역사           동학농민운동을 이끈 사람은?    전봉준
4   역사  문예 부흥이라는 중세 유럽에 일어난 운동은?   르네상스

## 모듈 종류 Setting

In [8]:
dataset_names = {
    'korquad1':'korquad1_model',
    'korquad2':'korquad2_model',
    'aihub':'aihub_model',
    'aihub':'aihub_korquad_model',
}

model_names={
    'bert' : 'bert',
    'hanbert':'hanbert',
    'kobert':'kobert'
}

In [18]:
def find_answer(question, qna_model, num_contents, wiki_converter, blog_converter):
    wiki_contents = get_wiki_data(question, num_contents)
    blog_contents = get_blog_data(question, num_contents)
    paragraphs = []
    for wiki_content in wiki_contents:
        temp_paragraphs = wiki_converter.convert_html(wiki_content)
        paragraphs.extend(temp_paragraphs)
    for blog_content in blog_contents:
        temp_paragraphs = blog_converter.convert_html(blog_content)
        paragraphs.extend(temp_paragraphs)
    
    result = ''
    if len(paragraphs) > 0:
        result = qna_model.get_answers(question, paragraphs)
    return result

## 1. 모델 테스트

In [14]:
## Converter INIT
wiki_converter = Korquad2_Converter(max_paragraph_length=1)
blog_converter = Blog_Converter(max_paragraph_length=1)

In [15]:
result_path = 'system_performance'
if not os.path.isdir(result_path):
    os.mkdir(result_path)

In [20]:
for dataset_name, dataset_path in dataset_names.items():
    for model_name, model_path in model_names.items():
        print(dataset_name, model_name)
        ## Set model_path
        temp_path = os.path.join(dataset_path, model_path)
        if dataset_name == 'korquad2':
            temp_path = os.path.join(dataset_path, model_path, 'step3', '4')
        
        ## Load QNA model
        qna_model = QuestionAnswerResponsor("../" + temp_path)
        test_df['contents_1'] = test_df.apply(lambda row: find_answer(row['question'], qna_model, 1, wiki_converter, blog_converter), axis=1)
        test_df['contents_5'] = test_df.apply(lambda row: find_answer(row['question'], qna_model, 5, wiki_converter, blog_converter), axis=1)
        
        csv_path = os.path.join(result_path, dataset_name + '_' + model_name + '.csv')
        test_df.to_csv(csv_path)

06/03/2020 20:08:50 - INFO - transformers.configuration_utils -   loading configuration file ../korquad1_model/bert/config.json
06/03/2020 20:08:50 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "directionality": "bidi",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num_fc_layers": 3,
  "pooler_size_per_head": 128,
  "pooler_type": "first_token_transform",
  "type_vocab_size": 2,
  "vocab_size": 119547
}

06/03/2020 20:08:50 - INFO - transformers.tokenization_utils -   Model name '../korquad1_model/bert' not found in model shortcut name list (bert-ba

korquad1 bert
EXAMPLE 변환시간 :  0.007756948471069336



convert squad examples to features: 100%|██████████| 1/1 [00:00<00:00,  2.64it/s]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 9986.44it/s]

Evaluating:   8%|▊         | 2/24 [00:00<00:01, 15.63it/s]

CONVERT에 걸린시간 :  0.6041302680969238



Evaluating: 100%|██████████| 24/24 [00:01<00:00, 17.66it/s]
06/03/2020 20:08:59 - INFO - korquad_metrics -   Writing predictions to: temp/predictions_.json
06/03/2020 20:08:59 - INFO - korquad_metrics -   Writing nbest to: temp/nbest_predictions_.json


...


Evaluating: 100%|██████████| 32/32 [00:01<00:00, 18.45it/s]
06/04/2020 01:33:24 - INFO - korquad_metrics -   Writing predictions to: temp/predictions_.json
06/04/2020 01:33:24 - INFO - korquad_metrics -   Writing nbest to: temp/nbest_predictions_.json


EXAMPLE 변환시간 :  0.02514338493347168



convert squad examples to features: 100%|██████████| 1/1 [00:01<00:00,  1.42s/it]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 4728.64it/s]

Evaluating:   4%|▎         | 2/57 [00:00<00:03, 16.09it/s]

CONVERT에 걸린시간 :  1.7657968997955322



Evaluating: 100%|██████████| 57/57 [00:03<00:00, 18.26it/s]
06/04/2020 01:33:34 - INFO - korquad_metrics -   Writing predictions to: temp/predictions_.json
06/04/2020 01:33:34 - INFO - korquad_metrics -   Writing nbest to: temp/nbest_predictions_.json


In [ ]:
## Set model_path
model_path = 'bert_multi/'
## 가져올 URL 갯수
num_contents = 5
## Load QNA model
qna_model = QuestionAnswerResponsor(model_path)
## Load wiki converter
wiki_converter = Korquad2_Converter(max_paragraph_length=1)
blog_converter = Blog_Converter(max_paragraph_length=1)

In [ ]:
def find_answer(question, qna_model, num_contents):
    wiki_contents = get_wiki_data(question, num_contents)
    blog_contents = get_blog_data(question, num_contents)
    paragraphs = []
    for wiki_content in wiki_contents:
        temp_paragraphs = wiki_converter.convert_html(wiki_content)
        paragraphs.extend(temp_paragraphs)
    for blog_content in blog_contents:
        temp_paragraphs = blog_converter.convert_html(blog_content)
        paragraphs.extend(temp_paragraphs)
    
    result = ''
    if len(paragraphs) > 0:
        result = qna_model.get_answers(question, paragraphs)
        result = result['text-01']
    return result